In [1]:
# %load_ext autoreload
# %autoreload 2

In [2]:
import os

import torch
import torchaudio as ta
from data_utils import data_to_df
from eval_utils import _normalize_text, _wer
from IPython.display import Audio

In [3]:
target_sr = 16000

In [4]:
video_dir = r'F:/BIG_FILES/AI_DATA/2024_STT'
if not os.path.exists(video_dir):
    print('Video directory not found')
    raise FileNotFoundError(video_dir)
    
cache_dir = './cache'
if not os.path.exists(cache_dir):
    os.makedirs(cache_dir)

In [5]:
video_df, segment_df = data_to_df(video_dir)
display(video_df.head(3), segment_df.head(3))

video_id                                 video_path  \
0  -9s7VmUX-10  F:/BIG_FILES/AI_DATA/2024_STT\-9s7VmUX-10   
1  0jh_-wVKeEE  F:/BIG_FILES/AI_DATA/2024_STT\0jh_-wVKeEE   
2  1GsU56ryNPU  F:/BIG_FILES/AI_DATA/2024_STT\1GsU56ryNPU   

                                     video_url language is_generated  \
0  https://www.youtube.com/watch?v=-9s7VmUX-10       de         True   
1  https://www.youtube.com/watch?v=0jh_-wVKeEE       de         True   
2  https://www.youtube.com/watch?v=1GsU56ryNPU       de         True   

   num_segments                                  segment_durations  
0            10  [32.030000000000086, 32.19, 29.129999999999995...  
1            10  [30.460000000000036, 30.99000000000001, 31.098...  
2            10  [30.69999999999999, 29.429999999999993, 30.710...

video_id  segment_id                                       segment_path  \
0  -9s7VmUX-10           0  F:/BIG_FILES/AI_DATA/2024_STT\-9s7VmUX-10\segm...   
1  -9s7VmUX-10           1  F:/BIG_FILES/AI_DATA/2024_STT\-9s7VmUX-10\segm...   
2  -9s7VmUX-10           2  F:/BIG_FILES/AI_DATA/2024_STT\-9s7VmUX-10\segm...   

                                     transcript_path  segment_duration  
0  F:/BIG_FILES/AI_DATA/2024_STT\-9s7VmUX-10\tran...             32.03  
1  F:/BIG_FILES/AI_DATA/2024_STT\-9s7VmUX-10\tran...             32.19  
2  F:/BIG_FILES/AI_DATA/2024_STT\-9s7VmUX-10\tran...             29.13

In [6]:
# load a random audio file
sample_segment = segment_df.sample(1).iloc[0]
audio_file_path = sample_segment['segment_path']
transcript_path = sample_segment['transcript_path']
is_generated = video_df[video_df['video_id'] == sample_segment['video_id']]['is_generated'].iloc[0]
with open(transcript_path, 'r', encoding="utf-8") as f:
    transcript = f.read().strip()
wave, sr = ta.load(audio_file_path)
print(f'Is generated: {is_generated}')
print(f'Loaded audio file: {audio_file_path}')
print(f'Wave shape: {wave.shape}')
print(f'Sample rate: {sr}')
display(Audio(wave.numpy(), rate=sr))

res_wave = ta.transforms.Resample(sr, target_sr)(wave)
print(f'Wave shape after resampling: {res_wave.shape}')
display(Audio(res_wave.numpy(), rate=target_sr))

# show the transcript but only x words per line
words = transcript.split()
words_per_line = 15
for i in range(0, len(words), words_per_line):
    print(' '.join(words[i:i+words_per_line]))

Is generated: False
Loaded audio file: F:/BIG_FILES/AI_DATA/2024_STT\Xbt61GHqKPg\segments\segment_00.mp3
Wave shape: torch.Size([1, 1412964])
Sample rate: 44100


Wave shape after resampling: torch.Size([1, 512640])


Ich habe sehr, sehr früh angefangen, ein Instrument zu spielen. Ich habe mit sechs Jahren,
glaube ich, Saxofon gespielt. Danach habe ich Klavier gespielt. Mein kleiner Bruder hat Geige gespielt,
meine Schwester hatte Kontrabass, glaube ich, Gitarre gespielt. Und meine Mutter hat zu Hause immer
gesungen, wir haben immer alle zusammen gesungen, ob marokkanische Lieder, arabische Lieder, Deutsch oder Französisch.
Englisch schon sehr, sehr viel. Ich habe angefangen, Rap zu hören, glaube ich. Mit zehn,
elf Jahren, mit Sexion d’Assaut, Maître Gims, Black M


In [7]:
def show_output(wave, sr, gt, decoded_output):
    display(Audio(wave.numpy(), rate=sr))
    print(f"Ground Truth: {gt}")
    print(f"Predicted:    {decoded_output.strip()}")
    print(f"---")
    print(f"Normalized Ground Truth: {_normalize_text(gt)}")
    print(f"Normalized Predicted:    {_normalize_text(decoded_output)}")
    print(f'WER: {_wer(gt, decoded_output, _normalize_text)}')

## Whisper

In [8]:
from transformers import (AutoProcessor, WhisperConfig,
                          WhisperForConditionalGeneration)

MODEL_ID = "openai/whisper-small"

In [9]:
whisper_config = WhisperConfig.from_pretrained(MODEL_ID, cache_dir=cache_dir)
whisper_model = WhisperForConditionalGeneration.from_pretrained(MODEL_ID, config=whisper_config, cache_dir=cache_dir)
whisper_model.eval().to('cuda')
whisper_processor = AutoProcessor.from_pretrained(MODEL_ID, cache_dir=cache_dir)

Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [10]:
inputs = whisper_processor(res_wave[0], return_tensors="pt", truncation=False, padding="longest", return_attention_mask=True, sampling_rate=target_sr)
inputs = inputs.to("cuda")
model_output = whisper_model.generate(**inputs, language="de")
decoded_output = whisper_processor.batch_decode(model_output, skip_special_tokens=True)[0]
show_output(res_wave, target_sr, transcript, decoded_output)

w:\Workspaces\Python\Studium\Master\speech2text\.venv\Lib\site-packages\transformers\models\whisper\modeling_whisper.py:694: UserWarning: 1Torch was not compiled with flash attention. (Triggered internally at ..\aten\src\ATen\native\transformers\cuda\sdp_utils.cpp:455.)
  attn_output = torch.nn.functional.scaled_dot_product_attention(


Ground Truth: Ich habe sehr, sehr früh angefangen, ein Instrument zu spielen. Ich habe mit sechs Jahren, glaube ich, Saxofon gespielt. Danach habe ich Klavier gespielt. Mein kleiner Bruder hat Geige gespielt, meine Schwester hatte Kontrabass, glaube ich, Gitarre gespielt. Und meine Mutter hat zu Hause immer gesungen, wir haben immer alle zusammen gesungen, ob marokkanische Lieder, arabische Lieder, Deutsch oder Französisch. Englisch schon sehr, sehr viel. Ich habe angefangen, Rap zu hören, glaube ich. Mit zehn, elf Jahren, mit Sexion d’Assaut, Maître Gims, Black M
Predicted:    Ich habe sehr früh angefangen, Instrumenten zu spielen. Ich habe mit sechs Jahren alt, glaube ich, Sacksofone gespielt. Danach habe ich Klavier, mein kleiner Bruder hat Geige gespielt. Meine Schwester hat Kontrabass, glaube ich, Gitarre gespielt. Und der Jahr, meine Mutter hat zu Hause immer gesungen. Wir haben immer alles zusammen gesungen. Ob Marokkanische Lieder, Arabische Lieder, Deutsch oder Französisch. En

## Wav2Vec2ForCTC

In [11]:
from transformers import Wav2Vec2ForCTC, Wav2Vec2Processor

MODEL_ID = "jonatasgrosman/wav2vec2-large-xlsr-53-german"

wav2vec_processor = Wav2Vec2Processor.from_pretrained(MODEL_ID, cache_dir=cache_dir)
wav2vec_model = Wav2Vec2ForCTC.from_pretrained(MODEL_ID, cache_dir=cache_dir)
_= wav2vec_model.eval().to('cuda')

Some weights of the model checkpoint at jonatasgrosman/wav2vec2-large-xlsr-53-german were not used when initializing Wav2Vec2ForCTC: ['wav2vec2.encoder.pos_conv_embed.conv.weight_g', 'wav2vec2.encoder.pos_conv_embed.conv.weight_v']
- This IS expected if you are initializing Wav2Vec2ForCTC from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing Wav2Vec2ForCTC from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of Wav2Vec2ForCTC were not initialized from the model checkpoint at jonatasgrosman/wav2vec2-large-xlsr-53-german and are newly initialized: ['wav2vec2.encoder.pos_conv_embed.conv.parametrizations.weight.original0', 'wav2vec2.encoder.pos_conv_embed.conv.parametrizations.weight.original1']
You

In [12]:
input_values = wav2vec_processor(res_wave[0], return_tensors="pt", sampling_rate=target_sr).input_values
with torch.no_grad():
    logits = wav2vec_model(input_values.to('cuda')).logits
predicted_ids = torch.argmax(logits, dim=-1)
predicted_sentences = wav2vec_processor.batch_decode(predicted_ids)[0]
show_output(res_wave, target_sr, transcript, predicted_sentences)

w:\Workspaces\Python\Studium\Master\speech2text\.venv\Lib\site-packages\torch\nn\modules\conv.py:306: UserWarning: Plan failed with a cudnnException: CUDNN_BACKEND_EXECUTION_PLAN_DESCRIPTOR: cudnnFinalize Descriptor Failed cudnn_status: CUDNN_STATUS_NOT_SUPPORTED (Triggered internally at ..\aten\src\ATen\native\cudnn\Conv_v8.cpp:919.)
  return F.conv1d(input, weight, bias, self.stride,


Ground Truth: Ich habe sehr, sehr früh angefangen, ein Instrument zu spielen. Ich habe mit sechs Jahren, glaube ich, Saxofon gespielt. Danach habe ich Klavier gespielt. Mein kleiner Bruder hat Geige gespielt, meine Schwester hatte Kontrabass, glaube ich, Gitarre gespielt. Und meine Mutter hat zu Hause immer gesungen, wir haben immer alle zusammen gesungen, ob marokkanische Lieder, arabische Lieder, Deutsch oder Französisch. Englisch schon sehr, sehr viel. Ich habe angefangen, Rap zu hören, glaube ich. Mit zehn, elf Jahren, mit Sexion d’Assaut, Maître Gims, Black M
Predicted:    ich hab sehr sehr früh angefangene instrument zu spielen ich haben mit sechs jahre alt gläubisch saxophon gespielt dann habe ich klavier mein kleiner bruder gaige gespielt äh meine schwester  kontrobars glaubisch gitarre gespielt unter ja meine mutter h zu hause immer gesungen wir haben immer alle zusammen hgesungen ob marokanische lieder ob arabische lieder deutsch oder französisch englischo sehr sehr viel ich 

## SeamlessM4Tv2

In [21]:
from transformers import AutoProcessor, SeamlessM4Tv2Model

MODEL_ID = "facebook/seamless-m4t-v2-large"

seamless_processor = AutoProcessor.from_pretrained(MODEL_ID, cache_dir=cache_dir)
seamless_model = SeamlessM4Tv2Model.from_pretrained(MODEL_ID, cache_dir=cache_dir)
_ = seamless_model.eval().to('cuda')

Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


Loading checkpoint shards:   0%|          | 0/2 [00:00<?, ?it/s]

In [34]:
# use the model for ASR
inputs = seamless_processor(audios=res_wave[0], return_tensors="pt", sampling_rate=target_sr)
inputs = inputs.to("cuda")
model_output = seamless_model.generate(**inputs, tgt_lang="deu", generate_speech=False)
decoded_output = seamless_processor.batch_decode(model_output[0], skip_special_tokens=True)[0]
show_output(res_wave, target_sr, transcript, decoded_output)

Ground Truth: Ich habe sehr, sehr früh angefangen, ein Instrument zu spielen. Ich habe mit sechs Jahren, glaube ich, Saxofon gespielt. Danach habe ich Klavier gespielt. Mein kleiner Bruder hat Geige gespielt, meine Schwester hatte Kontrabass, glaube ich, Gitarre gespielt. Und meine Mutter hat zu Hause immer gesungen, wir haben immer alle zusammen gesungen, ob marokkanische Lieder, arabische Lieder, Deutsch oder Französisch. Englisch schon sehr, sehr viel. Ich habe angefangen, Rap zu hören, glaube ich. Mit zehn, elf Jahren, mit Sexion d’Assaut, Maître Gims, Black M
Predicted:    Ich habe mit sechs Jahren Saxophon gespielt, dann Klavier, dann Geige, dann Kontrabass, dann Metrigems, dann Black Keys.
---
Normalized Ground Truth: ['ich', 'habe', 'sehr', 'sehr', 'frueh', 'angefangen', 'ein', 'instrument', 'zu', 'spielen', 'ich', 'habe', 'mit', 'sechs', 'jahren', 'glaube', 'ich', 'saxofon', 'gespielt', 'danach', 'habe', 'ich', 'klavier', 'gespielt', 'mein', 'kleiner', 'bruder', 'hat', 'geige'